In [6]:
import pandas as pd

# Загрузка обучающей выборки
train_df = pd.read_csv("trainee_train.csv")

In [7]:
# Подсчет количества уникальных значений в целевом признаке
target_counts = train_df["im"].value_counts()

# Вывод уникальных значений и их количества
print("Уникальные значения в целевом признаке 'im':")
print(target_counts)


Уникальные значения в целевом признаке 'im':
im
1.0    442
0.0    174
Name: count, dtype: int64


In [8]:
train_df['im'] = train_df['im'].astype(int)


In [9]:
from sklearn.model_selection import train_test_split

X = train_df.drop(columns=['im'])  # Признаки
y = train_df['im']  # Целевой признак
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

In [21]:
from sklearn.model_selection import GridSearchCV
from catboost import CatBoostClassifier
from sklearn.metrics import roc_auc_score
# Инициализируем модель
catboost = CatBoostClassifier()

param_grid = {
    'iterations': [100, 200, 300, 500, 1000],  # Количество деревьев
    'learning_rate': [0.01, 0.05, 0.1],  # Скорость обучения
    'depth': [4, 6, 8],  # Глубина деревьев
}

# Инициализируем GridSearch с кросс-валидацией и метрикой ROC AUC
grid_search = GridSearchCV(catboost, param_grid, cv=5, scoring='roc_auc')

# Запускаем GridSearch на обучающих данных
grid_search.fit(X_train, y_train)

# Получаем лучшие параметры
best_params = grid_search.best_params_
print("Лучшие параметры:", best_params)

# Получаем лучшую модель
best_model = grid_search.best_estimator_

# Оцениваем лучшую модель на тестовых данных
y_pred_proba = best_model.predict_proba(X_val)[:, 1]  # Вероятности класса 1
roc_auc = roc_auc_score(y_val, y_pred_proba)
print("ROC AUC лучшей модели на тестовых данных:", roc_auc)

0:	learn: 0.6864300	total: 8.26ms	remaining: 818ms
1:	learn: 0.6804719	total: 15.6ms	remaining: 765ms
2:	learn: 0.6762117	total: 21.7ms	remaining: 701ms
3:	learn: 0.6699428	total: 27.4ms	remaining: 658ms
4:	learn: 0.6622278	total: 32.9ms	remaining: 626ms
5:	learn: 0.6572115	total: 40.7ms	remaining: 638ms
6:	learn: 0.6531699	total: 46.5ms	remaining: 618ms
7:	learn: 0.6471941	total: 53ms	remaining: 609ms
8:	learn: 0.6414647	total: 58.9ms	remaining: 596ms
9:	learn: 0.6373211	total: 64ms	remaining: 576ms
10:	learn: 0.6325322	total: 69ms	remaining: 558ms
11:	learn: 0.6273215	total: 74.1ms	remaining: 543ms
12:	learn: 0.6207361	total: 78.7ms	remaining: 527ms
13:	learn: 0.6149215	total: 83.4ms	remaining: 512ms
14:	learn: 0.6096378	total: 88.5ms	remaining: 502ms
15:	learn: 0.6060550	total: 93.1ms	remaining: 489ms
16:	learn: 0.6021599	total: 98.1ms	remaining: 479ms
17:	learn: 0.5978438	total: 103ms	remaining: 468ms
18:	learn: 0.5931600	total: 108ms	remaining: 458ms
19:	learn: 0.5882397	total: 11

In [24]:
test_df = pd.read_csv("trainee_test_fish.csv")

# Получение прогнозов на тестовых данных
predictions = best_model.predict(test_df)

# Запись прогнозов в файл
with open("predictions.csv", "w") as f:
    f.write(",im\n")
    for i, pred in enumerate(predictions):
        f.write(f"{i},{float(pred)}\n")